# Ax Service API with RayTune on PyTorch CNN

Ax integrates easily with different scheduling frameworks and distributed training frameworks. In this example, Ax-driven optimization is executed in a distributed fashion using [RayTune](https://ray.readthedocs.io/en/latest/tune.html). 

RayTune is a scalable framework for hyperparameter tuning that provides many state-of-the-art hyperparameter tuning algorithms and seamlessly scales from laptop to distributed cluster with fault tolerance. RayTune leverages [Ray](https://ray.readthedocs.io/)'s Actor API to provide asynchronous parallel and distributed execution.

Ray 'Actors' are a simple and clean abstraction for replicating your Python classes across multiple workers and nodes. Each hyperparameter evaluation is asynchronously executed on a separate Ray actor and reports intermediate training progress back to RayTune. Upon reporting, RayTune then uses this information to performs actions such as early termination, re-prioritization, or checkpointing.

In [1]:
import logging

from ray import tune
from ray.tune import track
from ray.tune.suggest.ax import AxSearch

logger = logging.getLogger(tune.__name__)
logger.setLevel(
    level=logging.CRITICAL
)  # Reduce the number of Ray warnings that are not relevant here.

In [2]:
import numpy as np
import torch
from ax.plot.contour import plot_contour
from ax.plot.trace import optimization_trace_single_method
from ax.service.ax_client import AxClient
from ax.utils.notebook.plotting import init_notebook_plotting, render
from ax.utils.tutorials.cnn_utils import CNN, evaluate, load_mnist, train

init_notebook_plotting()

[INFO 11-04 18:40:44] ax.utils.notebook.plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


## 1. Initialize client
We specify `enforce_sequential_optimization` as False, because Ray runs many trials in parallel. With the sequential optimization enforcement, `AxClient` would expect the first few trials to be completed with data before generating more trials.

When high parallelism is not required, it is best to enforce sequential optimization, as it allows for achieving optimal results in fewer (but sequential) trials. In cases where parallelism is important, such as with distributed training using Ray, we choose to forego minimizing resource utilization and run more trials in parallel.

In [3]:
ax = AxClient(enforce_sequential_optimization=False)

[INFO 11-04 18:40:44] ax.service.ax_client: Starting optimization with verbose logging. To disable logging, set the `verbose_logging` argument to `False`. Note that float values in the logs are rounded to 2 decimal points.


## 2. Set up experiment
Here we set up the search space and specify the objective; refer to the Ax API tutorials for more detail.

In [4]:
ax.create_experiment(
    name="mnist_experiment",
    parameters=[
        {"name": "lr", "type": "range", "bounds": [1e-6, 0.4], "log_scale": True},
        {"name": "momentum", "type": "range", "bounds": [0.0, 1.0]},
    ],
    objective_name="mean_accuracy",
)

[INFO 11-04 18:40:44] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter lr. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.


[INFO 11-04 18:40:44] ax.service.utils.instantiation: Inferred value type of ParameterType.FLOAT for parameter momentum. If that is not the expected value type, you can explicity specify 'value_type' ('int', 'float', 'bool' or 'str') in parameter dict.


[INFO 11-04 18:40:44] ax.modelbridge.dispatch_utils: Using Bayesian Optimization generation strategy: GenerationStrategy(name='Sobol+GPEI', steps=[Sobol for 5 trials, GPEI for subsequent trials]). Iterations after 5 will take longer to generate due to  model-fitting.


## 3. Define how to evaluate trials
Since we use the Ax Service API here, we evaluate the parameterizations that Ax suggests, using RayTune. The evaluation function follows its usual pattern, taking in a parameterization and outputting an objective value. For detail on evaluation functions, see [Trial Evaluation](https://ax.dev/docs/runner.html). 

In [5]:
def train_evaluate(parameterization):
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    train_loader, valid_loader, test_loader = load_mnist(data_path="~/.data")
    net = train(
        net=CNN(),
        train_loader=train_loader,
        parameters=parameterization,
        dtype=torch.float,
        device=device,
    )
    track.log(
        mean_accuracy=evaluate(
            net=net,
            data_loader=valid_loader,
            dtype=torch.float,
            device=device,
        )
    )

## 4. Run optimization
Execute the Ax optimization and trial evaluation in RayTune using [AxSearch algorithm](https://ray.readthedocs.io/en/latest/tune-searchalg.html#ax-search):

In [6]:
tune.run(
    train_evaluate,
    num_samples=30,
    search_alg=AxSearch(ax_client=ax, max_concurrent=3),
    verbose=0,  # Set this level to 1 to see status updates and to 2 to also see trial results.
    # To use GPU, specify: resources_per_trial={"gpu": 1}.
)

2020-11-04 18:40:44,887	INFO services.py:1166 -- View the Ray dashboard at http://127.0.0.1:8265


[INFO 11-04 18:40:47] ax.service.ax_client: Generated new trial 0 with parameters {'lr': 0.0, 'momentum': 0.86}.


[INFO 11-04 18:40:47] ax.service.ax_client: Generated new trial 1 with parameters {'lr': 0.0, 'momentum': 0.25}.


[INFO 11-04 18:40:47] ax.service.ax_client: Generated new trial 2 with parameters {'lr': 0.0, 'momentum': 0.91}.


2020-11-04 18:40:47,431	WARNING worker.py:1072 -- Failed to unpickle actor class 'ImplicitFunc' for actor ID df5a1a8201000000. Traceback:
Traceback (most recent call last):
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
    actor_class = pickle.loads(pickled_class)
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
    from ray.tune.tune import run_experiments, run
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 5, in <module>
    from ray.tune.analysis import ExperimentAnalysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
    from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/experiment_analy

...

(pid=4784) 2020-11-04 18:41:01,585	ERROR function_manager.py:495 -- Failed to load actor class ImplicitFunc.
(pid=4784) Traceback (most recent call last):
(pid=4784)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
(pid=4784)     actor_class = pickle.loads(pickled_class)
(pid=4784)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
(pid=4784)     from ray.tune.tune import run_experiments, run
(pid=4784)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 5, in <module>
(pid=4784)     from ray.tune.analysis import ExperimentAnalysis
(pid=4784)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
(pid=4784)     from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
(pid=4784)   File "/home/travis/virt

2020-11-04 18:41:02,591	WARNING worker.py:1072 -- Failed to unpickle actor class 'ImplicitFunc' for actor ID 296a970401000000. Traceback:
Traceback (most recent call last):
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
    actor_class = pickle.loads(pickled_class)
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
    from ray.tune.tune import run_experiments, run
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 5, in <module>
    from ray.tune.analysis import ExperimentAnalysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
    from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
  File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/experiment_analy

(pid=4827) 2020-11-04 18:41:02,581	ERROR function_manager.py:495 -- Failed to load actor class ImplicitFunc.
(pid=4827) Traceback (most recent call last):
(pid=4827)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
(pid=4827)     actor_class = pickle.loads(pickled_class)
(pid=4827)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
(pid=4827)     from ray.tune.tune import run_experiments, run
(pid=4827)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 5, in <module>
(pid=4827)     from ray.tune.analysis import ExperimentAnalysis
(pid=4827)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
(pid=4827)     from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
(pid=4827)   File "/home/travis/virt

(pid=4828) 2020-11-04 18:41:02,637	ERROR function_manager.py:495 -- Failed to load actor class ImplicitFunc.
(pid=4828) Traceback (most recent call last):
(pid=4828)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/function_manager.py", line 493, in _load_actor_class_from_gcs
(pid=4828)     actor_class = pickle.loads(pickled_class)
(pid=4828)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/__init__.py", line 2, in <module>
(pid=4828)     from ray.tune.tune import run_experiments, run
(pid=4828)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/tune.py", line 5, in <module>
(pid=4828)     from ray.tune.analysis import ExperimentAnalysis
(pid=4828)   File "/home/travis/virtualenv/python3.7.1/lib/python3.7/site-packages/ray/tune/analysis/__init__.py", line 1, in <module>
(pid=4828)     from ray.tune.analysis.experiment_analysis import ExperimentAnalysis, Analysis
(pid=4828)   File "/home/travis/virt

TuneError: ('Trials did not complete', [train_evaluate_40de99b4, train_evaluate_40de99b5, train_evaluate_40de99b6, train_evaluate_40de99ba, train_evaluate_40de99bd, train_evaluate_40de99c0, train_evaluate_40de99c3, train_evaluate_423b1224, train_evaluate_423b1227, train_evaluate_423b122a, train_evaluate_423b122d, train_evaluate_4343b998, train_evaluate_4343b99b, train_evaluate_4343b99e, train_evaluate_4343b9a1, train_evaluate_446e43f5, train_evaluate_446e43f8, train_evaluate_446e43fb, train_evaluate_446e43fe, train_evaluate_45a19480, train_evaluate_45a19483, train_evaluate_45a19486, train_evaluate_4725842c, train_evaluate_4725842f, train_evaluate_47258432, train_evaluate_48110b2c, train_evaluate_48110b2f, train_evaluate_48110b32, train_evaluate_48110b35, train_evaluate_495895e2])

## 5. Retrieve the optimization results

In [7]:
best_parameters, values = ax.get_best_parameters()
best_parameters

{'lr': 0.001200477766990381, 'momentum': 0.6754525434808601}

In [8]:
means, covariances = values
means

{'mean_accuracy': 0.9713334434324482}

## 6. Plot the response surface and optimization trace

In [9]:
render(
    plot_contour(
        model=ax.generation_strategy.model,
        param_x="lr",
        param_y="momentum",
        metric_name="mean_accuracy",
    )
)

/Users/deriksson/opt/anaconda3/lib/python3.8/site-packages/ax/modelbridge/torch.py:311: UserWarning:

To copy construct from a tensor, it is recommended to use sourceTensor.clone().detach() or sourceTensor.clone().detach().requires_grad_(True), rather than torch.tensor(sourceTensor).



In [10]:
# `plot_single_method` expects a 2-d array of means, because it expects to average means from multiple
# optimization runs, so we wrap out best objectives array in another array.
best_objectives = np.array(
    [[trial.objective_mean * 100 for trial in ax.experiment.trials.values()]]
)
best_objective_plot = optimization_trace_single_method(
    y=np.maximum.accumulate(best_objectives, axis=1),
    title="Model performance vs. # of iterations",
    ylabel="Accuracy",
)
render(best_objective_plot)